# Analyzing simulation results

In the following tutorial, we will explore the analysis capabilities of `prodsys` for examining simulation results. In `prodsys`, every single of a simulation run get's tracked and logged, thus allowing to review the complete event log of a simulation run, as in the real world. Similarly, all KPIs can be calculated in the post processing. This allows for a very flexible analysis of the simulation results. `prodsys` allready provides many utility functions for calculating KPIs and plotting the results. In this tutorial, we will explore some of them.

For this example, we will use another production system which we will load from a json-file, which can be found in the examples folder of [prodsys' github page](https://github.com/sdm4fzi/prodsys). Download it and store it in the same folder as this notebook. Load the configuration and run a simulation with the following commands:

In [1]:
import prodsys

production_system = prodsys.adapters.JsonProductionSystemAdapter()	
production_system.read_data('example_configuration.json')

runner = prodsys.runner.Runner(adapter=production_system)
runner.initialize_simulation()
runner.run(20000)
runner.print_results()

100%|██████████| 20000/20000 [00:03<00:00, 5192.98it/s] 



------------- Throughput -------------

              Output  Throughput
Product_type                    
Product_1        158    1.040803
Product_2        113    0.744371
Product_3        154    1.014453
------------- WIP -------------

Product_type
Product_1    18.744155
Product_2    18.725161
Product_3    17.993283
Total        53.351869
Name: WIP, dtype: float64

------------- Throughput time -------------

Product_type
Product_1    568.297738
Product_2    722.492383
Product_3    567.056246
Name: Throughput_time, dtype: float64

------------- Resource states -------------

                    time_increment  resource_time  percentage
Resource Time_type                                           
R1       PR            6487.179816   19993.737408   32.446059
         SB            9402.143058   19993.737408   47.025440
         ST            2907.339730   19993.737408   14.541252
         UD            1197.074804   19993.737408    5.987249
R2       PR            9517.090415   19993.

When reviewing the simulation results, we will see that the production system consists of 4 prudction resources (R1, R2, R3, R4) and two transport resources (TR1, TR2). Additionally, we see that three different kind of products are produced (product_1, product_2, product_3). When reviewing the KPIs, there doesn't seem to be any problems with the production system. However, this is hard to tell without knowing something about the production system and we will see that there are some problems with the production system, which we will explore in the following.

The basic data structure used for logging all events can be accessed by the `EventLogger` class, which is an attribute of the runner. The logger stores this data in form of dictionaries but we can transform it to a pandas dataframe for more convenient analysis:

 which is why we will use some utiliy functions of the runner, to get a `PostProcessor` which stores the event log data in a pandas dataframe. 

In [2]:
df = runner.event_logger.get_data_as_dataframe()
df.head(10)

Time Resource             State                State Type   
0   7.608879       S1                S1      StateTypeEnum.source  \
1   7.608879      TR2               TP1   StateTypeEnum.transport   
2   8.925546      TR2               TP1   StateTypeEnum.transport   
3   8.925546      TR2               TP1   StateTypeEnum.transport   
4   9.242212      TR2               TP1   StateTypeEnum.transport   
5   9.242212       R4                P1  StateTypeEnum.production   
6  10.444744       R2  Breakdownstate_2   StateTypeEnum.breakdown   
7  12.243728       S2                S2      StateTypeEnum.source   
8  12.243728      TR1               TP1   StateTypeEnum.transport   
9  13.393728      TR1               TP1   StateTypeEnum.transport   

          Activity      Product  Expected End Time Target location  
0  created product  Product_1_0                NaN             NaN  
1      start state  Product_1_0           8.925546              S1  
2        end state  Product_1_0           8.925546              S1  
3      start state  Product_1_0           9.242212              R4  
4        end state  Product_1_0           9.242212              R4  
5      start state  Product_1_0          20.943956                  
6      start state                       25.444744                  
7  created product  Product_2_1                NaN             NaN  
8      start state  Product_2_1          13.393728              S2  
9        end state  Product_2_1          13.393728              S2

If we have a look at the dataframe, we will see that it contains 8 columns to describe each event:

- Time: The time of the event
- Resource: The resource on which the event occured
- State: The state of the resource that changed
- State Type: The type of the state that changed (e.g. source, transport, breakdwon, etc.)
- Activity: The activity that was performed
- Product: The product that was processed or transported (only for Production or Transport states)
- Expected End Time: The expected end time of the state
- Target location: The target location of a transport (only for Transport states)

Writing scripts that analysis these event logs can be tydious. We can use powerfull process mining tools to automate the analysis of these event logs to analysis all processes, event durations and so on. However, in this tutorial, we will focus on the analysis of the KPIs. For this, we will use the `PostProcessor` class, which can be obtained from runner. The `PostProcessor` class provides many utility functions for calculating KPIs and plotting the results. In this tutorial, we will explore some of them.
Let's get a `PostProcessor` from the runner and have a look at the KPIs:

In [3]:
post_processor = runner.get_post_processor()
print("Throughput per product type:", post_processor.get_aggregated_throughput_data())
print("WIP per product type:", post_processor.get_aggregated_wip_data())
print("Throughput time per product type:", post_processor.get_aggregated_throughput_time_data())

Throughput per product type: [158, 113, 154]
WIP per product type: [18.74415515409139, 18.725160929191155, 17.993283181085438]
Throughput time per product type: [568.2977376856611, 722.4923831037147, 567.056245912357]


`prodsys` also provides some models for KPIs which can be used more easily in algorithms. For example, we can use the `WIP_KPIs`property to calculate the KPI values of the production system:

In [4]:
for wip_kpi in post_processor.WIP_KPIs:
    print("WIP KPI:", wip_kpi)
    print("WIP KPI value:", wip_kpi.value)

WIP KPI: name=<KPIEnum.WIP: 'WIP'> target='min' weight=1 value=18.74415515409139 context=(<KPILevelEnum.PRODUCT_TYPE: 'product_type'>, <KPILevelEnum.SYSTEM: 'system'>) resource=None product_type='Product_1'
WIP KPI value: 18.74415515409139
WIP KPI: name=<KPIEnum.WIP: 'WIP'> target='min' weight=1 value=18.725160929191155 context=(<KPILevelEnum.PRODUCT_TYPE: 'product_type'>, <KPILevelEnum.SYSTEM: 'system'>) resource=None product_type='Product_2'
WIP KPI value: 18.725160929191155
WIP KPI: name=<KPIEnum.WIP: 'WIP'> target='min' weight=1 value=17.993283181085438 context=(<KPILevelEnum.PRODUCT_TYPE: 'product_type'>, <KPILevelEnum.SYSTEM: 'system'>) resource=None product_type='Product_3'
WIP KPI value: 17.993283181085438
WIP KPI: name=<KPIEnum.WIP: 'WIP'> target='min' weight=1 value=53.35186888535831 context=(<KPILevelEnum.ALL_PRODUCTS: 'all_products'>, <KPILevelEnum.SYSTEM: 'system'>) resource=None product_type='all_products'
WIP KPI value: 53.35186888535831


The `PostProcessor` also provides some pre-processed data frames, which can be used for custom analyis. For example, we can get a data frame with only products that have been finished during the simulation run:

In [5]:
post_processor.df_finished_product.head()

Time Resource State                State Type         Activity   
0  7.608879       S1    S1      StateTypeEnum.source  created product  \
1  7.608879      TR2   TP1   StateTypeEnum.transport      start state   
2  8.925546      TR2   TP1   StateTypeEnum.transport        end state   
3  8.925546      TR2   TP1   StateTypeEnum.transport      start state   
4  9.242212       R4    P1  StateTypeEnum.production      start state   

       Product  Expected End Time Target location   
0  Product_1_0                NaN             NaN  \
1  Product_1_0           8.925546              S1   
2  Product_1_0           8.925546              S1   
3  Product_1_0           9.242212              R4   
4  Product_1_0          20.943956                   

                       DateTime   Combined_activity Product_type   
0 1970-01-01 00:07:36.532740426  S1 created product    Product_1  \
1 1970-01-01 00:07:36.532740426     TP1 start state    Product_1   
2 1970-01-01 00:08:55.532740426       TP1 end state    Product_1   
3 1970-01-01 00:08:55.532740426     TP1 start state    Product_1   
4 1970-01-01 00:09:14.532740426      P1 start state    Product_1   

        State_type  State_sorting_Index  
0  Interface State                    2  
1    Process State                    5  
2    Process State                    4  
3    Process State                    5  
4    Process State                    5

However, most easiest or fastest^method for analysing simulation results is using the plotting functionalities of `prodsys`. These can be accesses through the `kpi_visualization` and only require a `PostProcessor` for instantiation. For example, we can plot the time percentages of resources in different states:

In [6]:
from prodsys.util import kpi_visualization

kpi_visualization.plot_time_per_state_of_resources(post_processor)

We can observe, that the resources in the production system are not really heavily utilized, since their productive (PR) percentage is lower than 50%. Let's plot the WIP KPI and see if this aligns with our first observations:

In [7]:
from prodsys.util import kpi_visualization

kpi_visualization.plot_WIP(post_processor)

We can see that the production system has at first a stable WIP at around a total of 10 but at roughly 3000 minutes, the WIP suddenly increases and does not stabilize anymore. This suggest, that our system is running very full with semi-finished material. Let's also look at the throughput time of the products:

In [8]:
kpi_visualization.plot_throughput_time_over_time(post_processor)

Again, we see a divergence of throughput time over simualted time. Here, the Start_time relates to the start of production of a product, i.e. the creation at it's source. These observations suggest, that the system is running to a WIP level which cannot be processed efficiently, similar to a crowded parking space after an event. If we take a look at the queue's of the system and the capacity of production resources, we can determine the maximal number of products in the system:

In [9]:
capacity = 0
for resource in production_system.resource_data:
    capacity += resource.capacity

for queue in production_system.queue_data:
    capacity += queue.capacity

print(capacity)

69


We see, that at maximum 69 products can be in the production system in parallel. However, when we examine the queues more in detail, we see, that some resource share also queues (R3 and R4):

In [10]:
machines = prodsys.adapters.get_machines(production_system)
for machine in machines:
    print(machine.ID, machine.input_queues, machine.output_queues)

R1 ['IQ1'] ['OQ1']
R2 ['IQ9'] ['OQ2']
R3 ['IQ2'] ['OQ3']
R4 ['IQ2'] ['OQ3']


Let's investigate if the production system's storage capacity for products is too low that there is some blocking or if the production system's throughput is not high enough for the arrival processes. To do this, we test how the WIP changes if we make the queues of the production system unlimited (capacity=0).

In [14]:
adjusted_production_system = production_system.copy(deep=True)

for queue in adjusted_production_system.queue_data:
    queue.capacity = 0

runner = prodsys.runner.Runner(adapter=adjusted_production_system)
runner.initialize_simulation()
runner.run(20000)
new_post_processor = runner.get_post_processor()
kpi_visualization.plot_WIP(new_post_processor)


  0%|          | 0/20000 [00:00<?, ?it/s]

100%|██████████| 20000/20000 [00:03<00:00, 5279.03it/s]


If we look at the results again, we see that the production system WIP increases even stronger without limited queues. This suggests that both cases were True. At first, the production system got fuller without limited queues which suggest that some queues overflowed when limited causing some blocking. Additionally, we see that the WIP still increases over time, thus the production system requires more resources or another configuration to satisfy the arrival processes. `prodsys` provides also some functionality to optimize production system configuration. See the optimization example for more detailed information. 